# Neighborhood comparison New York-Toronto

### Import neccessary libraries

In [4]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!pip install folium 
import folium # map rendering library

print('Libraries imported.')

     |████████████████████████████████| 102kB 7.7MB/s ta 0:00:011
Libraries imported.


### Getting New York Neighborhoods Data

In [7]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)
neighborhoods_data = newyork_data['features']

# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 
# instantiate the dataframe
ny_neighborhoods = pd.DataFrame(columns=column_names)

for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    ny_neighborhoods = ny_neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)
ny_neighborhoods.head()

Data downloaded!


Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

#### Create a map of New York with neighborhoods superimposed on top.

In [8]:
address = 'New York City, NY'
geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(ny_neighborhoods['Latitude'], ny_neighborhoods['Longitude'], ny_neighborhoods['Borough'], ny_neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


### Getting Toronto Neighborhoods Data

##### Getting info from Wikipedia

In [9]:
import numpy as np # library to handle data in a vectorized manner
import pandas as pd # library for data analsysis

toronto_neighborhoods = pd.read_html("https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M")[0]
toronto_neighborhoods.head()

Postal Code           Borough               Neighborhood
0         M1A      Not assigned               Not assigned
1         M2A      Not assigned               Not assigned
2         M3A        North York                  Parkwoods
3         M4A        North York           Victoria Village
4         M5A  Downtown Toronto  Regent Park, Harbourfront

#### Remove Not assigned Borough

In [10]:
toronto_neighborhoods = toronto_neighborhoods[toronto_neighborhoods['Borough'] != 'Not assigned']

#### Read CSV with coordinates

In [11]:
df_coor = pd.read_csv("http://cocl.us/Geospatial_data")
df_coor.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

##### Join Toronto neighborhoods with Coordinates table

In [ ]:
toronto_neighborhoods = toronto_neighborhoods.join(df_coor.set_index('Postal Code'), on='Postal Code')

In [14]:
toronto_neighborhoods.head()

Postal Code           Borough                                 Neighborhood  \
2         M3A        North York                                    Parkwoods   
3         M4A        North York                             Victoria Village   
4         M5A  Downtown Toronto                    Regent Park, Harbourfront   
5         M6A        North York             Lawrence Manor, Lawrence Heights   
6         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   

    Latitude  Longitude  
2  43.753259 -79.329656  
3  43.725882 -79.315572  
4  43.654260 -79.360636  
5  43.718518 -79.464763  
6  43.662301 -79.389494

## Create Toronto Map

In [15]:
address = 'Toronto, Ontario'

geolocator = Nominatim(user_agent="toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto, Ontario are {}, {}.'.format(latitude, longitude))

# create map of Manhattan using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(toronto_neighborhoods['Latitude'], toronto_neighborhoods['Longitude'], toronto_neighborhoods['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

The geograpical coordinate of Toronto, Ontario are 43.6534817, -79.3839347.


# Define Foursquare Credentials and Version

In [16]:
CLIENT_ID = 'GK3B04EMBTZPDIOXFOMMLGEB0NOYG1KXPD2U2VTTWS20KGOA' # your Foursquare ID
CLIENT_SECRET = 'KTYNA02JNAMIPD1MYUOE3Q2DHONRQYXTWSNKRH0EZEECDZNY' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: GK3B04EMBTZPDIOXFOMMLGEB0NOYG1KXPD2U2VTTWS20KGOA
CLIENT_SECRET:KTYNA02JNAMIPD1MYUOE3Q2DHONRQYXTWSNKRH0EZEECDZNY


##### Function to get venues categories

In [17]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [51]:
# function to get nearby venues
def getNearbyVenues(names, latitudes, longitudes, radius=500, LIMIT=100):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
        ready = False
        while not ready:
            # make the GET request
            req = requests.get(url)
            if 'groups' in req.json()["response"]:
                results = req.json()["response"]['groups'][0]['items']
                ready = True
        
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

###  Get nearby venues to NY neighborhoods

In [19]:
ny_venues = getNearbyVenues(names=ny_neighborhoods['Neighborhood'],
                                   latitudes=ny_neighborhoods['Latitude'],
                                   longitudes=ny_neighborhoods['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

###  Get nearby venues to Toronto neighborhoods

In [28]:
toronto_venues = getNearbyVenues(names=toronto_neighborhoods['Neighborhood'],
                                   latitudes=toronto_neighborhoods['Latitude'],
                                   longitudes=toronto_neighborhoods['Longitude']
                                  )

Parkwoods
Victoria Village
Regent Park, Harbourfront
Lawrence Manor, Lawrence Heights
Queen's Park, Ontario Provincial Government
Islington Avenue, Humber Valley Village
Malvern, Rouge
Don Mills
Parkview Hill, Woodbine Gardens
Garden District, Ryerson
Glencairn
West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale
Rouge Hill, Port Union, Highland Creek
Don Mills
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate, Bloordale Gardens, Old Burnhamthorpe, Markland Wood
Guildwood, Morningside, West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor, Wilson Heights, Downsview North
Thorncliffe Park
Richmond, Adelaide, King
Dufferin, Dovercourt Village
Scarborough Village
Fairview, Henry Farm, Oriole
Northwood Park, York University
East Toronto, Broadview North (Old East York)
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
Kennedy Park, Ionview, East Birchmo

In [29]:
toronto_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2  Victoria Village              43.725882              -79.315572   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                    Venue  Venue Latitude  Venue Longitude  \
0         Brookbanks Park       43.751976       -79.332140   
1           Variety Store       43.751974       -79.333114   
2  Victoria Village Arena       43.723481       -79.315635   
3               Portugril       43.725819       -79.312785   
4             Tim Hortons       43.725517       -79.313103   

          Venue Category  
0                   Park  
1      Food & Drink Shop  
2           Hockey Arena  
3  Portuguese Restaurant  
4            Coffee Shop

##  Analyze Each Neighborhood in New York

In [46]:
# one hot encoding
ny_onehot = pd.get_dummies(ny_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
ny_onehot['Neighborhood'] = ny_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [ny_onehot.columns[-1]] + list(ny_onehot.columns[:-1])
ny_onehot = ny_onehot[fixed_columns]

ny_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  \
0            0                  0               0                  0   
1            0                  0               0                  0   
2            0                  0               0                  0   
3            0                  0               0                  0   
4            0                  0               0                  0   

   African Restaurant  Airport Terminal  American Restaurant  Antique Shop  \
0                   0                 0                    0             0   
1                   0                 0                    0             0   
2                   0                 0                    0             0   
3                   0                 0                    0             0   
4                   0                 0                    0             0   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0                 0                       0            0           0   
1       0                 0                       0            0           0   
2       0                 0                       0            0           0   
3       0                 0                       0            0           0   
4       0                 0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   Automotive Shop  BBQ Joint  Baby Store  Badminton Court  Bagel Shop  \
0                0          0           0                0           0   
1                0          0           0                0           0   
2                0          0           0                0           0   
3                0          0           0                0           0   
4                0          0           0                0           0   

   Bakery  Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0       0     0    0               0                 0                 0   
1       0     0    0               0                 0                 0   
2       0     0    0               0                 0                 0   
3       0     0    0               0                 0                 0   
4       0     0    0               0                 0                 0   

   Basketball Stadium  Bath House  Beach  Beach Bar  Bed & Breakfast  \
0                   0           0      0          0                0   
1                   0           0      0          0                0   
2                   0           0      0          0                0   
3                   0           0      0          0                0   
4                   0           0      0          0                0   

   Beer Bar  Beer Garden  Beer Store  Big Box Store  Bike Rental / Bike Share  \
0         0            0           0              0                         0   
1         0            0           0              0                         0   
2         0            0           0              0                         0   
3         0            0           0              0                         0

In [32]:
ny_grouped = ny_onehot.groupby('Neighborhood').mean().reset_index()
ny_grouped.head()

Neighborhood  Yoga Studio  Accessories Store  Adult Boutique  \
0       Allerton          0.0                0.0             0.0   
1       Annadale          0.0                0.0             0.0   
2  Arden Heights          0.0                0.0             0.0   
3      Arlington          0.0                0.0             0.0   
4       Arrochar          0.0                0.0             0.0   

   Afghan Restaurant  African Restaurant  Airport Terminal  \
0                0.0                 0.0               0.0   
1                0.0                 0.0               0.0   
2                0.0                 0.0               0.0   
3                0.0                 0.0               0.0   
4                0.0                 0.0               0.0   

   American Restaurant  Antique Shop  Arcade  Arepa Restaurant  \
0             0.000000           0.0     0.0               0.0   
1             0.000000           0.0     0.0               0.0   
2             0.000000           0.0     0.0               0.0   
3             0.142857           0.0     0.0               0.0   
4             0.000000           0.0     0.0               0.0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                     0.0          0.0         0.0                  0.0   
1                     0.0          0.0         0.0                  0.0   
2                     0.0          0.0         0.0                  0.0   
3                     0.0          0.0         0.0                  0.0   
4                     0.0          0.0         0.0                  0.0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  Auditorium  \
0                   0.0               0.0                0.00         0.0   
1                   0.0               0.0                0.00         0.0   
2                   0.0               0.0                0.00         0.0   
3                   0.0               0.0                0.00         0.0   
4                   0.0               0.0                0.05         0.0   

   Australian Restaurant  Austrian Restaurant  Automotive Shop  BBQ Joint  \
0                    0.0                  0.0              0.0        0.0   
1                    0.0                  0.0              0.0        0.0   
2                    0.0                  0.0              0.0        0.0   
3                    0.0                  0.0              0.0        0.0   
4                    0.0                  0.0              0.0        0.0   

   Baby Store  Badminton Court  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0         0.0              0.0        0.00     0.0   0.0  0.0             0.0   
1         0.0              0.0        0.00     0.0   0.0  0.0             0.0   
2         0.0              0.0        0.00     0.0   0.0  0.0             0.0   
3         0.0              0.0        0.00     0.0   0.0  0.0             0.0   
4         0.0              0.0        0.05     0.0   0.0  0.0             0.0   

   Baseball Stadium  Basketball Court  Basketball Stadium  Bath House  Beach  \
0               0.0               0.0                 0.0         0.0    0.0   
1               0.0               0.0                 0.0         0.0    0.0   
2               0.0               0.0                 0.0         0.0    0.0   
3               0.0               0.0                 0.0         0.0    0.0   
4               0.0               0.0                 0.0         0.0    0.0   

   Beach Bar  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0        0.0              0.0       0.0          0.0         0.0   
1        0.0              0.0       0.0          0.0         0.0   
2        0.0              0.0       0.0          0.0         0.0   
3        0.0              0.0       0.0          0.0         0.0   
4        0.0              0.0       0.0          0.0         0.0   

   Big Box Store  Bike Rental / Bike Share  Bike Shop  Bike Trail  Bist

In [33]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [34]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
ny_neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
ny_neighborhoods_venues_sorted['Neighborhood'] = ny_grouped['Neighborhood']

for ind in np.arange(ny_grouped.shape[0]):
    ny_neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(ny_grouped.iloc[ind, :], num_top_venues)

ny_neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Allerton           Pizza Place         Deli / Bodega   
1       Annadale                  Food                 Diner   
2  Arden Heights                 Hotel              Pharmacy   
3      Arlington              Bus Stop         Deli / Bodega   
4       Arrochar         Deli / Bodega    Italian Restaurant   

  3rd Most Common Venue 4th Most Common Venue      5th Most Common Venue  \
0      Department Store        Cosmetics Shop                Supermarket   
1           Pizza Place         Train Station                        Pub   
2            Smoke Shop           Coffee Shop                Pizza Place   
3          Intersection          Liquor Store              Boat or Ferry   
4              Bus Stop           Pizza Place  Middle Eastern Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                   Spa          Intersection  Fast Food Restaurant   
1            Sports Bar            Restaurant          Liquor Store   
2                 Field           Event Space               Exhibit   
3   American Restaurant         Women's Store  Fast Food Restaurant   
4            Food Truck              Pharmacy          Liquor Store   

  9th Most Common Venue 10th Most Common Venue  
0    Mexican Restaurant            Gas Station  
1              Pharmacy                   Farm  
2            Eye Doctor                Factory  
3   Filipino Restaurant                  Field  
4            Bagel Shop         Sandwich Place

##  Analyze Each Neighborhood in Toronto

In [35]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Yoga Studio  Accessories Store  Airport  Airport Food Court  Airport Gate  \
0            0                  0        0                   0             0   
1            0                  0        0                   0             0   
2            0                  0        0                   0             0   
3            0                  0        0                   0             0   
4            0                  0        0                   0             0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Antique Shop  Aquarium  Art Gallery  Art Museum  Arts & Crafts Store  \
0             0         0            0           0                    0   
1             0         0            0           0                    0   
2             0         0            0           0                    0   
3             0         0            0           0                    0   
4             0         0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auto Workshop  BBQ Joint  Baby Store  \
0                 0                   0              0          0           0   
1                 0                   0              0          0           0   
2                 0                   0              0          0           0   
3                 0                   0              0          0           0   
4                 0                   0              0          0           0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0           0       0     0    0               0                 0   
1           0       0     0    0               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    0               0                 0   
4           0       0     0    0               0                 0   

   Basketball Court  Basketball Stadium  Beach  Bed & Breakfast  Beer Bar  \
0                 0                   0      0                0         0   
1                 0                   0      0                0         0   
2                 0                   0      0                0         0   
3                 0                   0      0                0         0   
4                 0                   0      0                0         0   

   Beer Store  Belgian Restaurant  Bike Shop  Bistro  Boat or Ferry  \
0           0                   0          0       0              0   
1           0                   0          0       0              0   
2           0                   0          0       0              0   
3           0                   0          0       0              0   
4           0                   0          0       0              0   

   Bookstore  Boutique  Brazilian Restaurant  Breakfast Spot  Brewery  \
0          0         0                     0               0        0   
1          0         0                     0               0        0   
2          0         0                     0               0        0   
3          0         0                     0               0        0   
4          0         0                     0               0        0   

   Bridal Shop  Bubble Tea Shop  Building  Burger Joint  Burrito Place  \
0            0                0         0             0              0   
1            0                0         0             0              0   
2            0                0         0             0              0   
3            0                0         0             0              0   
4

In [36]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped.head()

Neighborhood  Yoga Studio  \
0                                        Agincourt          0.0   
1                           Alderwood, Long Branch          0.0   
2  Bathurst Manor, Wilson Heights, Downsview North          0.0   
3                                  Bayview Village          0.0   
4                Bedford Park, Lawrence Manor East          0.0   

   Accessories Store  Airport  Airport Food Court  Airport Gate  \
0                0.0      0.0                 0.0           0.0   
1                0.0      0.0                 0.0           0.0   
2                0.0      0.0                 0.0           0.0   
3                0.0      0.0                 0.0           0.0   
4                0.0      0.0                 0.0           0.0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0             0.0              0.0               0.0                 0.00   
1             0.0              0.0               0.0                 0.00   
2             0.0              0.0               0.0                 0.00   
3             0.0              0.0               0.0                 0.00   
4             0.0              0.0               0.0                 0.04   

   Antique Shop  Aquarium  Art Gallery  Art Museum  Arts & Crafts Store  \
0           0.0       0.0          0.0         0.0                  0.0   
1           0.0       0.0          0.0         0.0                  0.0   
2           0.0       0.0          0.0         0.0                  0.0   
3           0.0       0.0          0.0         0.0                  0.0   
4           0.0       0.0          0.0         0.0                  0.0   

   Asian Restaurant  Athletics & Sports  Auto Workshop  BBQ Joint  Baby Store  \
0               0.0                 0.0            0.0        0.0         0.0   
1               0.0                 0.0            0.0        0.0         0.0   
2               0.0                 0.0            0.0        0.0         0.0   
3               0.0                 0.0            0.0        0.0         0.0   
4               0.0                 0.0            0.0        0.0         0.0   

   Bagel Shop  Bakery      Bank  Bar  Baseball Field  Baseball Stadium  \
0         0.0     0.0  0.000000  0.0             0.0               0.0   
1         0.0     0.0  0.000000  0.0             0.0               0.0   
2         0.0     0.0  0.105263  0.0             0.0               0.0   
3         0.0     0.0  0.250000  0.0             0.0               0.0   
4         0.0     0.0  0.000000  0.0             0.0               0.0   

   Basketball Court  Basketball Stadium  Beach  Bed & Breakfast  Beer Bar  \
0               0.0                 0.0    0.0              0.0       0.0   
1               0.0                 0.0    0.0              0.0       0.0   
2               0.0                 0.0    0.0              0.0       0.0   
3               0.0                 0.0    0.0              0.0       0.0   
4               0.0                 0.0    0.0              0.0       0.0   

   Beer Store  Belgian Restaurant  Bike Shop  Bistro  Boat or Ferry  \
0         0.0                 0.0        0.0     0.0            0.0   
1         0.0                 0.0        0.0     0.0            0.0   
2         0.0                 0.0        0.0     0.0            0.0   
3         0.0                 0.0        0.0     0.0            0.0   
4         0.0                 0.0        0.0     0.0            0.0   

   Bookstore  Boutique  Brazilian Restaurant  Breakfast Spot  Brewery  \
0        0.0       0.0                   0.0            0.25      0.0   
1        0.0       0.0                   0.0            0.00      0.0   
2        0.0       0.0                   0.0            0.00      0.0   
3        0.0       0.0                   0.0            0.00      0.0   
4        0.0       0.0                   0.0            0.00      0.0   

   Bridal Shop  Bubble Tea Shop  Building  Burger Joint  

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [37]:

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
toronto_neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
toronto_neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    toronto_neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

toronto_neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                                        Agincourt                Lounge   
1                           Alderwood, Long Branch           Pizza Place   
2  Bathurst Manor, Wilson Heights, Downsview North                  Bank   
3                                  Bayview Village                  Café   
4                Bedford Park, Lawrence Manor East           Coffee Shop   

       2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0  Latin American Restaurant          Skating Rink        Breakfast Spot   
1                        Gym           Coffee Shop          Dance Studio   
2                Coffee Shop     Mobile Phone Shop        Sandwich Place   
3                       Bank   Japanese Restaurant    Chinese Restaurant   
4             Sandwich Place    Italian Restaurant       Thai Restaurant   

       5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0                    Dog Run          Dessert Shop    Dim Sum Restaurant   
1                   Pharmacy          Skating Rink        Sandwich Place   
2  Middle Eastern Restaurant           Supermarket            Restaurant   
3              Women's Store      Department Store    Dim Sum Restaurant   
4                 Restaurant           Pizza Place              Pharmacy   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0                 Diner        Discount Store    Distribution Center  
1                   Pub         Women's Store           Dessert Shop  
2        Ice Cream Shop         Deli / Bodega    Fried Chicken Joint  
3                 Diner        Discount Store    Distribution Center  
4                  Café     Indian Restaurant                    Pub

# Join New York data with Toronto data

In [48]:
df = pd.concat([ny_neighborhoods, toronto_neighborhoods], ignore_index=True, sort=False)
df.tail()

Borough                                       Neighborhood  \
404         Etobicoke      The Kingsway, Montgomery Road, Old Mill North   
405  Downtown Toronto                               Church and Wellesley   
406      East Toronto  Business reply mail Processing Centre, South C...   
407         Etobicoke  Old Mill South, King's Mill Park, Sunnylea, Hu...   
408         Etobicoke  Mimico NW, The Queensway West, South of Bloor,...   

      Latitude  Longitude Postal Code  
404  43.653654 -79.506944         M8X  
405  43.665860 -79.383160         M4Y  
406  43.662744 -79.321558         M7Y  
407  43.636258 -79.498509         M8Y  
408  43.628841 -79.520999         M8Z

## Get Narby Venues

In [52]:
df_venues = getNearbyVenues(names=df['Neighborhood'],
                                   latitudes=df['Latitude'],
                                   longitudes=df['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [53]:
df_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1         Walgreens       40.896528       -73.844700        Pharmacy  
2  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
3          Rite Aid       40.896649       -73.844846        Pharmacy  
4           Dunkin'       40.890459       -73.849089      Donut Shop

## Analyze each neighborhood

In [75]:
# one hot encoding
df_onehot = pd.get_dummies(df_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
df_onehot['Neighborhood'] = df_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [df_onehot.columns[-1]] + list(df_onehot.columns[:-1])
df_onehot = df_onehot[fixed_columns]

df_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  \
0            0                  0               0                  0   
1            0                  0               0                  0   
2            0                  0               0                  0   
3            0                  0               0                  0   
4            0                  0               0                  0   

   African Restaurant  Airport  Airport Food Court  Airport Gate  \
0                   0        0                   0             0   
1                   0        0                   0             0   
2                   0        0                   0             0   
3                   0        0                   0             0   
4                   0        0                   0             0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Antique Shop  Aquarium  Arcade  Arepa Restaurant  Argentinian Restaurant  \
0             0         0       0                 0                       0   
1             0         0       0                 0                       0   
2             0         0       0                 0                       0   
3             0         0       0                 0                       0   
4             0         0       0                 0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Arts & Entertainment  \
0            0           0                    0                     0   
1            0           0                    0                     0   
2            0           0                    0                     0   
3            0           0                    0                     0   
4            0           0                    0                     0   

   Asian Restaurant  Athletics & Sports  Auditorium  Australian Restaurant  \
0                 0                   0           0                      0   
1                 0                   0           0                      0   
2                 0                   0           0                      0   
3                 0                   0           0                      0   
4                 0                   0           0                      0   

   Austrian Restaurant  Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  \
0                    0              0                0          0           0   
1                    0              0                0          0           0   
2                    0              0                0          0           0   
3                    0              0                0          0           0   
4                    0              0                0          0           0   

   Badminton Court  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0                0           0       0     0    0               0   
1                0           0       0     0    0               0   
2                0           0       0     0    0               0   
3                0           0       0     0    0               0   
4                0           0       0     0    0               0   

   Baseball Stadium  Basketball Court  Basketball Stadium  Bath House  Beach  \
0                 0                 0                   0           0      0   
1                 0                 0                   0           0      0   
2                 0                 0                   0           0      0   
3                 0                 0                   0           0      0   
4            

In [76]:
df_grouped = df_onehot.groupby('Neighborhood').mean().reset_index()
df_grouped.head()

Neighborhood  Yoga Studio  Accessories Store  Adult Boutique  \
0               Agincourt          0.0                0.0             0.0   
1  Alderwood, Long Branch          0.0                0.0             0.0   
2                Allerton          0.0                0.0             0.0   
3                Annadale          0.0                0.0             0.0   
4           Arden Heights          0.0                0.0             0.0   

   Afghan Restaurant  African Restaurant  Airport  Airport Food Court  \
0                0.0                 0.0      0.0                 0.0   
1                0.0                 0.0      0.0                 0.0   
2                0.0                 0.0      0.0                 0.0   
3                0.0                 0.0      0.0                 0.0   
4                0.0                 0.0      0.0                 0.0   

   Airport Gate  Airport Lounge  Airport Service  Airport Terminal  \
0           0.0             0.0              0.0               0.0   
1           0.0             0.0              0.0               0.0   
2           0.0             0.0              0.0               0.0   
3           0.0             0.0              0.0               0.0   
4           0.0             0.0              0.0               0.0   

   American Restaurant  Antique Shop  Aquarium  Arcade  Arepa Restaurant  \
0                  0.0           0.0       0.0     0.0               0.0   
1                  0.0           0.0       0.0     0.0               0.0   
2                  0.0           0.0       0.0     0.0               0.0   
3                  0.0           0.0       0.0     0.0               0.0   
4                  0.0           0.0       0.0     0.0               0.0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                     0.0          0.0         0.0                  0.0   
1                     0.0          0.0         0.0                  0.0   
2                     0.0          0.0         0.0                  0.0   
3                     0.0          0.0         0.0                  0.0   
4                     0.0          0.0         0.0                  0.0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  Auditorium  \
0                   0.0               0.0                 0.0         0.0   
1                   0.0               0.0                 0.0         0.0   
2                   0.0               0.0                 0.0         0.0   
3                   0.0               0.0                 0.0         0.0   
4                   0.0               0.0                 0.0         0.0   

   Australian Restaurant  Austrian Restaurant  Auto Workshop  Automotive Shop  \
0                    0.0                  0.0            0.0              0.0   
1                    0.0                  0.0            0.0              0.0   
2                    0.0                  0.0            0.0              0.0   
3                    0.0                  0.0            0.0              0.0   
4                    0.0                  0.0            0.0              0.0   

   BBQ Joint  Baby Store  Badminton Court  Bagel Shop  Bakery  Bank  Bar  \
0        0.0         0.0              0.0         0.0     0.0   0.0  0.0   
1        0.0         0.0              0.0         0.0     0.0   0.0  0.0   
2        0.0         0.0              0.0         0.0     0.0   0.0  0.0   
3        0.0         0.0              0.0         0.0     0.0   0.0  0.0   
4        0.0         0.0              0.0         0.0     0.0   0.0  0.0   

   Baseball Field  Baseball Stadium  Basketball Court  Basketball Stadium  \
0             0.0               0.0               0.0                 0.0   
1             0.0               0.0               0.0                 0.0   
2             0.0               0.0               0.0                 0.0   
3             0.0               0.0               0.0              

In [62]:
df_grouped

Neighborhood  Yoga Studio  \
0                                            Agincourt     0.000000   
1                               Alderwood, Long Branch     0.000000   
2                                             Allerton     0.000000   
3                                             Annadale     0.000000   
4                                        Arden Heights     0.000000   
5                                            Arlington     0.000000   
6                                             Arrochar     0.000000   
7                                              Arverne     0.000000   
8                                              Astoria     0.000000   
9                                      Astoria Heights     0.000000   
10                                          Auburndale     0.000000   
11                                          Bath Beach     0.000000   
12     Bathurst Manor, Wilson Heights, Downsview North     0.000000   
13                                   Battery Park City     0.000000   
14                                           Bay Ridge     0.000000   
15                                         Bay Terrace     0.000000   
16                                          Baychester     0.000000   
17                                             Bayside     0.013699   
18                                           Bayswater     0.000000   
19                                     Bayview Village     0.000000   
20                                        Bedford Park     0.000000   
21                   Bedford Park, Lawrence Manor East     0.000000   
22                                  Bedford Stuyvesant     0.000000   
23                                          Beechhurst     0.066667   
24                                            Bellaire     0.000000   
25                                        Belle Harbor     0.000000   
26                                           Bellerose     0.000000   
27                                             Belmont     0.000000   
28                                         Bensonhurst     0.000000   
29                                         Berczy Park     0.000000   
30                                        Bergen Beach     0.000000   
31                         Birch Cliff, Cliffside West     0.000000   
32                                          Blissville     0.000000   
33                                          Bloomfield     0.000000   
34                                         Boerum Hill     0.022727   
35                                        Borough Park     0.000000   
36                                        Breezy Point     0.000000   
37                                           Briarwood     0.000000   
38                                      Brighton Beach     0.000000   
39                                       Broad Channel     0.000000   
40                                   Broadway Junction     0.000000   
41        Brockton, Parkdale Village, Exhibition Place     0.041667   
42                                           Bronxdale     0.000000   
43                                    Brooklyn Heights     0.040000   
44                                          Brookville     0.000000   
45                                         Brownsville     0.000000   
46                                          Bulls Head     0.000000   
47                                            Bushwick     0.000000   
48   Business reply mail Processing Centre, South C...     0.000000   
49                                        Butler Manor     0.000000   
50   CN Tower, King and Spadina, Railway Lands, Har...     0.000000   
51                                 Caledonia-Fairbanks     0.000000   
52                                     Cambria Heights     0.000000   
53               Canada Post Gateway Processing Centre     0.000000   
54                                            Canarsie     0.000000   
55                                       Carnegie Hill     0.03296

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [120]:
# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
df_neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
df_neighborhoods_venues_sorted['Neighborhood'] = df_grouped['Neighborhood']

for ind in np.arange(df_grouped.shape[0]):
    df_neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(df_grouped.iloc[ind, :], num_top_venues)

df_neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0               Agincourt        Breakfast Spot          Skating Rink   
1  Alderwood, Long Branch           Pizza Place                   Pub   
2                Allerton           Pizza Place         Deli / Bodega   
3                Annadale                   Pub            Restaurant   
4           Arden Heights           Pizza Place            Smoke Shop   

       3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0  Latin American Restaurant                Lounge               Factory   
1                   Pharmacy        Sandwich Place          Dance Studio   
2             Cosmetics Shop                   Spa      Department Store   
3                 Sports Bar          Liquor Store              Pharmacy   
4                      Hotel              Pharmacy           Coffee Shop   

         6th Most Common Venue 7th Most Common Venue  \
0  Eastern European Restaurant   Egyptian Restaurant   
1                  Coffee Shop          Skating Rink   
2                  Supermarket     Martial Arts Dojo   
3                Train Station                 Diner   
4                Women's Store        Duty-free Shop   

         8th Most Common Venue        9th Most Common Venue  \
0            Electronics Store          Empanada Restaurant   
1                          Gym  Eastern European Restaurant   
2                   Donut Shop           Chinese Restaurant   
3                  Pizza Place                         Food   
4  Eastern European Restaurant          Egyptian Restaurant   

  10th Most Common Venue  
0     English Restaurant  
1    Egyptian Restaurant  
2     Mexican Restaurant  
3           Cycle Studio  
4      Electronics Store

# Cluster Neighborhoods

In [121]:
# set number of clusters
kclusters = 3

df_grouped_clustering = df_grouped.drop('Neighborhood', 1)
df_grouped_clustering.head()

Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  \
0          0.0                0.0             0.0                0.0   
1          0.0                0.0             0.0                0.0   
2          0.0                0.0             0.0                0.0   
3          0.0                0.0             0.0                0.0   
4          0.0                0.0             0.0                0.0   

   African Restaurant  Airport  Airport Food Court  Airport Gate  \
0                 0.0      0.0                 0.0           0.0   
1                 0.0      0.0                 0.0           0.0   
2                 0.0      0.0                 0.0           0.0   
3                 0.0      0.0                 0.0           0.0   
4                 0.0      0.0                 0.0           0.0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0             0.0              0.0               0.0                  0.0   
1             0.0              0.0               0.0                  0.0   
2             0.0              0.0               0.0                  0.0   
3             0.0              0.0               0.0                  0.0   
4             0.0              0.0               0.0                  0.0   

   Antique Shop  Aquarium  Arcade  Arepa Restaurant  Argentinian Restaurant  \
0           0.0       0.0     0.0               0.0                     0.0   
1           0.0       0.0     0.0               0.0                     0.0   
2           0.0       0.0     0.0               0.0                     0.0   
3           0.0       0.0     0.0               0.0                     0.0   
4           0.0       0.0     0.0               0.0                     0.0   

   Art Gallery  Art Museum  Arts & Crafts Store  Arts & Entertainment  \
0          0.0         0.0                  0.0                   0.0   
1          0.0         0.0                  0.0                   0.0   
2          0.0         0.0                  0.0                   0.0   
3          0.0         0.0                  0.0                   0.0   
4          0.0         0.0                  0.0                   0.0   

   Asian Restaurant  Athletics & Sports  Auditorium  Australian Restaurant  \
0               0.0                 0.0         0.0                    0.0   
1               0.0                 0.0         0.0                    0.0   
2               0.0                 0.0         0.0                    0.0   
3               0.0                 0.0         0.0                    0.0   
4               0.0                 0.0         0.0                    0.0   

   Austrian Restaurant  Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  \
0                  0.0            0.0              0.0        0.0         0.0   
1                  0.0            0.0              0.0        0.0         0.0   
2                  0.0            0.0              0.0        0.0         0.0   
3                  0.0            0.0              0.0        0.0         0.0   
4                  0.0            0.0              0.0        0.0         0.0   

   Badminton Court  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0              0.0         0.0     0.0   0.0  0.0             0.0   
1              0.0         0.0     0.0   0.0  0.0             0.0   
2              0.0         0.0     0.0   0.0  0.0             0.0   
3              0.0         0.0     0.0   0.0  0.0             0.0   
4              0.0         0.0     0.0   0.0  0.0             0.0   

   Baseball Stadium  Basketball Court  Basketball Stadium  Bath House  Beach  \
0               0.0               0.0                 0.0         0.0    0.0   
1               0.0               0.0                 0.0         0.0    0.0   
2               0.0               0.0                 0.0         0.0    0.0   
3               0.0               0.0                 0.0         0.0    0.0   
4            

In [122]:
# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(df_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 2, 2, 2, 2, 1, 2, 1, 1, 2], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [123]:
# add clustering labels
df_neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

df_merged = df

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
df_merged = df_merged.join(df_neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')
df_merged = df_merged[df_merged['Cluster Labels'].notna()]

df_merged.head() # check the last columns!

Borough Neighborhood   Latitude  Longitude Postal Code  Cluster Labels  \
0   Bronx    Wakefield  40.894705 -73.847201         NaN             2.0   
1   Bronx   Co-op City  40.874294 -73.829939         NaN             2.0   
2   Bronx  Eastchester  40.887556 -73.827806         NaN             2.0   
3   Bronx    Fieldston  40.895437 -73.905643         NaN             2.0   
4   Bronx    Riverdale  40.890834 -73.912585         NaN             2.0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0              Pharmacy            Donut Shop         Deli / Bodega   
1                  Park           Bus Station         Grocery Store   
2  Caribbean Restaurant           Bus Station         Deli / Bodega   
3        Cosmetics Shop                 River                 Plaza   
4           Bus Station                  Park                   Gym   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0           Gas Station        Sandwich Place            Laundromat   
1        Baseball Field      Basketball Court              Pharmacy   
2                 Diner     Food & Drink Shop             Juice Bar   
3           Bus Station           Flea Market               Factory   
4                  Bank        Baseball Field          Home Service   

         7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0                 Dessert Shop                  Food        Ice Cream Shop   
1               Discount Store           Pizza Place            Restaurant   
2           Chinese Restaurant    Seafood Restaurant       Automotive Shop   
3  Eastern European Restaurant   Egyptian Restaurant     Electronics Store   
4                        Plaza               Exhibit           Event Space   

  10th Most Common Venue  
0            Curling Ice  
1             Bagel Shop  
2          Metro Station  
3    Empanada Restaurant  
4   Ethiopian Restaurant

In [124]:
df_merged['Cluster Labels'].value_counts()

2.0    198
1.0    195
0.0     12
Name: Cluster Labels, dtype: int64

In [125]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(df_merged['Latitude'], df_merged['Longitude'], df_merged['Neighborhood'], df_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## Analyzing Cluster 0

In [127]:
df0 = df_merged.loc[df_merged['Cluster Labels'] == 0, df_merged.columns[[1] + list(range(5, df_merged.shape[1]))]]

In [130]:
df0.head()

Neighborhood  Cluster Labels 1st Most Common Venue  \
27    Clason Point             0.0                  Park   
192     Somerville             0.0                  Park   
203      Todt Hill             0.0                  Park   
256  Randall Manor             0.0                  Park   
306      Parkwoods             0.0     Food & Drink Shop   

    2nd Most Common Venue 3rd Most Common Venue        4th Most Common Venue  \
27      Convenience Store                  Pool                Grocery Store   
192         Women's Store   Dumpling Restaurant  Eastern European Restaurant   
203         Women's Store   Dumpling Restaurant  Eastern European Restaurant   
256              Bus Stop           Pizza Place                   Bagel Shop   
306                  Park         Women's Store                      Factory   

           5th Most Common Venue 6th Most Common Venue  \
27                      Bus Stop   American Restaurant   
192          Egyptian Restaurant     Electronics Store   
203          Egyptian Restaurant     Electronics Store   
256          Egyptian Restaurant     Electronics Store   
306  Eastern European Restaurant   Egyptian Restaurant   

         7th Most Common Venue 8th Most Common Venue  \
27   South American Restaurant         Boat or Ferry   
192        Empanada Restaurant    English Restaurant   
203        Empanada Restaurant    English Restaurant   
256        Empanada Restaurant    English Restaurant   
306          Electronics Store   Empanada Restaurant   

          9th Most Common Venue 10th Most Common Venue  
27   Financial or Legal Service             Eye Doctor  
192       Entertainment Service   Ethiopian Restaurant  
203       Entertainment Service   Ethiopian Restaurant  
256       Entertainment Service   Ethiopian Restaurant  
306          English Restaurant  Entertainment Service

In [128]:
df0['1st Most Common Venue'].value_counts()

Park                 9
Food & Drink Shop    1
Convenience Store    1
Playground           1
Name: 1st Most Common Venue, dtype: int64

In [129]:
df0['2nd Most Common Venue'].value_counts()

Women's Store        4
Park                 3
Convenience Store    2
Swim School          1
Bus Stop             1
River                1
Name: 2nd Most Common Venue, dtype: int64

In [131]:
df0['3rd Most Common Venue'].value_counts()

Dumpling Restaurant    3
Pizza Place            2
Pool                   2
Women's Store          2
Falafel Restaurant     1
Electronics Store      1
Bus Line               1
Name: 3rd Most Common Venue, dtype: int64

In [153]:
df0_toronto_count = 0
df0_ny_count = 0
for neigh in df0['Neighborhood'].values:
    if neigh in toronto_neighborhoods['Neighborhood'].values:
        df0_toronto_count += 1
    else:
        df0_ny_count += 1

print("Cluster 0 Country Count")
print("New York: {}".format(df0_ny_count))
print("Toronto: {}".format(df0_toronto_count))

Cluster 0 Country Count
New York: 4
Toronto: 8


## Analyzing Cluster 1

In [132]:
df1 = df_merged.loc[df_merged['Cluster Labels'] == 1, df_merged.columns[[1] + list(range(5, df_merged.shape[1]))]]

In [133]:
df1.head()

Neighborhood  Cluster Labels      1st Most Common Venue  \
9   Williamsbridge             1.0          Convenience Store   
12     City Island             1.0         Seafood Restaurant   
22     Port Morris             1.0  Latin American Restaurant   
28     Throgs Neck             1.0                Coffee Shop   
39  Edgewater Park             1.0         Italian Restaurant   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
9                Nightclub  Caribbean Restaurant                   Bar   
12  Thrift / Vintage Store         Jewelry Store          Liquor Store   
22  Furniture / Home Store            Donut Shop    Spanish Restaurant   
28                     Bar    Italian Restaurant           Pizza Place   
39             Pizza Place        Ice Cream Shop      Asian Restaurant   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
9          Metro Station            Soup Place           Fish Market   
12        Baseball Field                   Bar                  Bank   
22            Restaurant   Peruvian Restaurant            Distillery   
28     Mobile Phone Shop             Juice Bar   American Restaurant   
39         Deli / Bodega           Coffee Shop            Donut Shop   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
9             Eye Doctor     Electronics Store                   Food  
12                  Park       Harbor / Marina             Smoke Shop  
22            Food Truck      Storage Facility                Brewery  
28         Deli / Bodega            Sports Bar       Asian Restaurant  
39                  Park  Fast Food Restaurant             Sports Bar

In [135]:
df1['1st Most Common Venue'].value_counts().head()

Coffee Shop           27
Italian Restaurant    20
Bar                   16
Café                  10
Park                   9
Name: 1st Most Common Venue, dtype: int64

In [136]:
df1['2nd Most Common Venue'].value_counts().head()

Coffee Shop           24
Park                  11
Café                   9
Women's Store          8
Italian Restaurant     8
Name: 2nd Most Common Venue, dtype: int64

In [137]:
df1['3rd Most Common Venue'].value_counts().head()

Bar                    12
Coffee Shop            11
Café                    9
American Restaurant     8
Pizza Place             8
Name: 3rd Most Common Venue, dtype: int64

In [152]:
df1_toronto_count = 0
df1_ny_count = 0
for neigh in df1['Neighborhood'].values:
    if neigh in toronto_neighborhoods['Neighborhood'].values:
        df1_toronto_count += 1
    else:
        df1_ny_count += 1

print("Cluster 1 Country Count")
print("New York: {}".format(df1_ny_count))
print("Toronto: {}".format(df1_toronto_count))

Cluster 1 Country Count
New York: 125
Toronto: 70


## Analyzing Cluster 2

In [138]:
df2 = df_merged.loc[df_merged['Cluster Labels'] == 2, df_merged.columns[[1] + list(range(5, df_merged.shape[1]))]]

In [139]:
df2.head()

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0    Wakefield             2.0              Pharmacy            Donut Shop   
1   Co-op City             2.0                  Park           Bus Station   
2  Eastchester             2.0  Caribbean Restaurant           Bus Station   
3    Fieldston             2.0        Cosmetics Shop                 River   
4    Riverdale             2.0           Bus Station                  Park   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0         Deli / Bodega           Gas Station        Sandwich Place   
1         Grocery Store        Baseball Field      Basketball Court   
2         Deli / Bodega                 Diner     Food & Drink Shop   
3                 Plaza           Bus Station           Flea Market   
4                   Gym                  Bank        Baseball Field   

  6th Most Common Venue        7th Most Common Venue 8th Most Common Venue  \
0            Laundromat                 Dessert Shop                  Food   
1              Pharmacy               Discount Store           Pizza Place   
2             Juice Bar           Chinese Restaurant    Seafood Restaurant   
3               Factory  Eastern European Restaurant   Egyptian Restaurant   
4          Home Service                        Plaza               Exhibit   

  9th Most Common Venue 10th Most Common Venue  
0        Ice Cream Shop            Curling Ice  
1            Restaurant             Bagel Shop  
2       Automotive Shop          Metro Station  
3     Electronics Store    Empanada Restaurant  
4           Event Space   Ethiopian Restaurant

In [140]:
df2['1st Most Common Venue'].value_counts().head()

Pizza Place             37
Chinese Restaurant      15
Bank                    12
Grocery Store           10
Caribbean Restaurant    10
Name: 1st Most Common Venue, dtype: int64

In [141]:
df2['2nd Most Common Venue'].value_counts().head()

Pizza Place      22
Deli / Bodega    18
Grocery Store    10
Pharmacy          8
Donut Shop        7
Name: 2nd Most Common Venue, dtype: int64

In [142]:
df2['3rd Most Common Venue'].value_counts().head()

Pizza Place           13
Bakery                12
Bank                  10
Chinese Restaurant    10
Pharmacy               9
Name: 3rd Most Common Venue, dtype: int64

#### And we check country count

In [151]:
df2_toronto_count = 0
df2_ny_count = 0
for neigh in df2['Neighborhood'].values:
    if neigh in toronto_neighborhoods['Neighborhood'].values:
        df2_toronto_count += 1
    else:
        df2_ny_count += 1

print("Cluster 2 Country Count")
print("New York: {}".format(df2_ny_count))
print("Toronto: {}".format(df2_toronto_count))


Cluster 2 Country Count
New York: 176
Toronto: 22


### Country Distribution

In [156]:
print("New York")
print("Cluster 0: {} -- {}%".format(df0_ny_count, round(df0_ny_count/(df0_ny_count + df1_ny_count + df2_ny_count)*100)))
print("Cluster 1 {} -- {}%".format(df1_ny_count, round(df1_ny_count/(df0_ny_count + df1_ny_count + df2_ny_count)*100)))
print("Cluster 2 {} -- {}%".format(df2_ny_count, round(df2_ny_count/(df0_ny_count + df1_ny_count + df2_ny_count)*100)))

New York
Cluster 0: 4 -- 1%
Cluster 1 125 -- 41%
Cluster 2 176 -- 58%


In [157]:
print("Toronto")
print("Cluster 0: {} -- {}%".format(df0_toronto_count, round(df0_toronto_count/(df0_toronto_count + df1_toronto_count + df2_toronto_count)*100)))
print("Cluster 1 {} -- {}%".format(df1_toronto_count, round(df1_toronto_count/(df0_toronto_count + df1_toronto_count + df2_toronto_count)*100)))
print("Cluster 2 {} -- {}%".format(df2_toronto_count, round(df2_toronto_count/(df0_toronto_count + df1_toronto_count + df2_toronto_count)*100)))

Toronto
Cluster 0: 8 -- 8%
Cluster 1 70 -- 70%
Cluster 2 22 -- 22%
